<a href="https://colab.research.google.com/github/celine-y/Voice-Clone-Subtitles/blob/master/Voice_Clone.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
# Clone git repo
!git clone https://github.com/CorentinJ/Real-Time-Voice-Cloning.git

Cloning into 'Real-Time-Voice-Cloning'...
remote: Enumerating objects: 2351, done.
remote: Total 2351 (delta 0), reused 0 (delta 0), pack-reused 2351
Receiving objects: 100% (2351/2351), 360.95 MiB | 34.05 MiB/s, done.
Resolving deltas: 100% (1291/1291), done.


In [0]:
cd Real-Time-Voice-Cloning/

/content/Real-Time-Voice-Cloning


In [0]:
# Install dependencies
!pip install -q -r requirements.txt
!pip install -q srt
!pip install -q ffmpeg
!pip install -q mutagen
!pip install -q pydub
!apt-get install -qq libportaudio2
!pip install synthesizer

     |████████████████████████████████| 377.0MB 44kB/s 
     |████████████████████████████████| 686kB 32.4MB/s 
     |████████████████████████████████| 71kB 9.2MB/s 
     |████████████████████████████████| 245kB 44.5MB/s 
     |████████████████████████████████| 62.2MB 124kB/s 
     |████████████████████████████████| 491kB 51.6MB/s 
     |████████████████████████████████| 3.2MB 50.5MB/s 
     |████████████████████████████████| 204kB 51.2MB/s 
     |████████████████████████████████| 266kB 48.7MB/s 
ERROR: tensorflow 1.15.0 has requirement tensorboard<1.16.0,>=1.15.0, but you'll have tensorboard 1.14.0 which is incompatible.
ERROR: tensorflow 1.15.0 has requirement tensorflow-estimator==1.15.1, but you'll have tensorflow-estimator 1.14.0 which is incompatible.
     |████████████████████████████████| 931kB 6.5MB/s 
Selecting previously unselected package libportaudio2:amd64.
(Reading database ... 132681 files and directories currently installed.)
Preparing to unpack .../libportaudio2_19.6.

In [0]:
# Download dataset
!gdown https://drive.google.com/uc?id=1n1sPXvT34yXFLT47QZA6FIRGrwMeSsZc
!unzip pretrained.zip

Downloading...
From: https://drive.google.com/uc?id=1n1sPXvT34yXFLT47QZA6FIRGrwMeSsZc
To: /content/Real-Time-Voice-Cloning/pretrained.zip
384MB [00:02, 131MB/s]
Archive:  pretrained.zip
   creating: encoder/saved_models/
  inflating: encoder/saved_models/pretrained.pt  
   creating: synthesizer/saved_models/
   creating: synthesizer/saved_models/logs-pretrained/
   creating: synthesizer/saved_models/logs-pretrained/taco_pretrained/
 extracting: synthesizer/saved_models/logs-pretrained/taco_pretrained/checkpoint  
  inflating: synthesizer/saved_models/logs-pretrained/taco_pretrained/tacotron_model.ckpt-278000.data-00000-of-00001  
  inflating: synthesizer/saved_models/logs-pretrained/taco_pretrained/tacotron_model.ckpt-278000.index  
  inflating: synthesizer/saved_models/logs-pretrained/taco_pretrained/tacotron_model.ckpt-278000.meta  
   creating: vocoder/saved_models/
   creating: vocoder/saved_models/pretrained/
  inflating: vocoder/saved_models/pretrained/pretrained.pt  


In [0]:
# Code for recording audio from the browser
from IPython.display import Javascript
from google.colab import output
from base64 import b64decode
import IPython
import uuid
from google.colab import output


class InvokeButton(object):
  def __init__(self, title, callback):
    self._title = title
    self._callback = callback

  def _repr_html_(self):
    from google.colab import output
    callback_id = 'button-' + str(uuid.uuid4())
    output.register_callback(callback_id, self._callback)

    template = """<button id="{callback_id}" style="cursor:pointer;background-color:#EEEEEE;border-color:#E0E0E0;padding:5px 15px;font-size:14px">{title}</button>
        <script>
          document.querySelector("#{callback_id}").onclick = (e) => {{
            google.colab.kernel.invokeFunction('{callback_id}', [], {{}})
            e.preventDefault();
          }};
        </script>"""
    html = template.format(title=self._title, callback_id=callback_id)
    return html

RECORD = """
const sleep  = time => new Promise(resolve => setTimeout(resolve, time))
const b2text = blob => new Promise(resolve => {
  const reader = new FileReader()
  reader.onloadend = e => resolve(e.srcElement.result)
  reader.readAsDataURL(blob)
})
var record = time => new Promise(async resolve => {
  stream = await navigator.mediaDevices.getUserMedia({ audio: true })
  recorder = new MediaRecorder(stream)
  chunks = []
  recorder.ondataavailable = e => chunks.push(e.data)
  recorder.start()
  await sleep(time)
  recorder.onstop = async ()=>{
    blob = new Blob(chunks)
    text = await b2text(blob)
    resolve(text)
  }
  recorder.stop()
})
"""

def record(sec=3):
  display(Javascript(RECORD))
  s = output.eval_js('record(%d)' % (sec*1000))
  b = b64decode(s.split(',')[1])
  with open('audio.wav','wb+') as f:
    f.write(b)
  return 'audio.wav'

In [0]:
from IPython.display import Audio
from IPython.utils import io
from synthesizer.inference import Synthesizer
from encoder import inference as encoder
from vocoder import inference as vocoder
from pathlib import Path
import numpy as np
import librosa
encoder_weights = Path("encoder/saved_models/pretrained.pt")
vocoder_weights = Path("vocoder/saved_models/pretrained/pretrained.pt")
syn_dir = Path("synthesizer/saved_models/logs-pretrained/taco_pretrained")
encoder.load_model(encoder_weights)
synthesizer = Synthesizer(syn_dir)
vocoder.load_model(vocoder_weights)

Loaded encoder "pretrained.pt" trained to step 1564501
Found synthesizer "pretrained" trained to step 278000
Building Wave-RNN
Trainable Parameters: 4.481M
Loading model weights at vocoder/saved_models/pretrained/pretrained.pt


In [0]:
import wave
import scipy.io.wavfile as sp_wav

def synth(text="Hello world", source_voice_path="obama.wav"):
  in_fpath = Path(source_voice_path)
  reprocessed_wav = encoder.preprocess_wav(in_fpath)
  original_wav, sampling_rate = librosa.load(in_fpath)
  preprocessed_wav = encoder.preprocess_wav(original_wav, sampling_rate)
  embed = encoder.embed_utterance(preprocessed_wav)
  print("Synthesizing new audio...")
  with io.capture_output() as captured:
    specs = synthesizer.synthesize_spectrograms([text], [embed])
  generated_wav = vocoder.infer_waveform(specs[0])
  generated_wav = np.pad(generated_wav, (0, synthesizer.sample_rate), mode="constant")

  print(str(synthesizer.sample_rate))
  display(Audio(generated_wav, rate=synthesizer.sample_rate))

  print(type(generated_wav))
  out_filename = str(uuid.uuid4())
  sp_wav.write(out_filename +'.wav', synthesizer.sample_rate, generated_wav)

  return out_filename

#Stitching Subtitles Together

In [0]:
!pip install -q srt
!pip install -q ffmpeg
!pip install -q mutagen
!pip install -q pydub

In [0]:
import srt
import requests
import argparse
from mutagen.mp3 import MP3
from pydub import AudioSegment
import ffmpeg
import io
import IPython.display as ipd
# from synthesizer import Synthesizer
import numpy as np

from google.colab import drive, files
# drive.mount('/content/drive')

In [0]:
def fit_audio(audio_path, duration):
  t_req = duration.total_seconds()
  audio = AudioSegment.from_file(audio_path +'.wav', format="wav") #TODO: get format of audio
  a_length = audio.duration_seconds
  extra_time = t_req - a_length 
  print("Duration of audio: " + str(a_length))
  print("Extra time needed: " + str(extra_time))
  if extra_time > 0:
    # mp3 is too short, append some blank noise
    print("Too short")
    final_audio = append_time(audio, extra_time)
  else:
    # mp3 is too long, speed up
    print("Too long")
    final_audio = speed_up(audio, t_req)

  return final_audio

In [0]:
def append_time(audio, extra_time):
  # create extra_time sec of silence audio segment
  extra_audio = AudioSegment.silent(duration=extra_time)
  return audio + extra_audio

In [0]:
def speed_up(audio, time_required):
  print(int(time_required))
  print(int(audio.duration_seconds))
  playback_speed = audio.duration_seconds/time_required
  print("Speedup: " + str(playback_speed))
  audio_stream = AudioSegment.speedup(audio, playback_speed)

  time_needed = time_required - audio_stream.duration_seconds
  if time_needed > 0:
    audio_stream = append_time(audio_stream, time_needed)
  return audio_stream

In [0]:
import librosa

uploaded = files.upload()
for fn in uploaded.keys():
  f = uploaded[fn].decode("utf-8")
  subtitle_generator = srt.parse(f)
  output_audio = None
  for subtitle in subtitle_generator:
    audio_path = synth(text=subtitle.content, source_voice_path='kimmy.wav')
    y, s = librosa.load(audio_path +'.wav', sr=8000)
    sp_wav.write('new.wav', 8000, y)
    duration = subtitle.end - subtitle.start
    if output_audio:
      output_audio += fit_audio('new', duration)
    else:
      output_audio = fit_audio('new', duration)
    print("New Time: "+ str(output_audio.duration_seconds))
  output_audio.export('output.wav', format='wav')

Saving English (1).srt to English (1) (2).srt
Synthesizing new audio...
{| ████████████████ 47500/48000 | Batch Size: 5 | Gen Rate: 4.1kHz | }16000


<class 'numpy.ndarray'>
Duration of audio: 3.7375
Extra time needed: -2.3674999999999997
Too long
1
3
Speedup: 2.7281021897810214
New Time: 1.513
Synthesizing new audio...
{| ████████████████ 66500/67200 | Batch Size: 7 | Gen Rate: 6.0kHz | }16000


<class 'numpy.ndarray'>
Duration of audio: 4.7875
Extra time needed: -1.4374999999999996
Too long
3
4
Speedup: 1.4291044776119401
New Time: 4.918
Synthesizing new audio...
{| ████████████████ 66500/67200 | Batch Size: 7 | Gen Rate: 6.2kHz | }16000


<class 'numpy.ndarray'>
Duration of audio: 4.4125
Extra time needed: -0.7124999999999995
Too long
3
4
Speedup: 1.1925675675675673
New Time: 8.683
Synthesizing new audio...
{| ████████████████ 66500/67200 | Batch Size: 7 | Gen Rate: 6.3kHz | }16000


<class 'numpy.ndarray'>
Duration of audio: 4.8125
Extra time needed: -1.2625000000000002
Too long
3
4
Speedup: 1.3556338028169015
New Time: 12.301
Synthesizing new audio...
{| ████████████████ 76000/76800 | Batch Size: 8 | Gen Rate: 7.1kHz | }16000


...

<class 'numpy.ndarray'>
Duration of audio: 4.85
Extra time needed: -0.13999999999999968
Too long
4
4
Speedup: 1.029723991507431
New Time: 70.96879818594104
Synthesizing new audio...
{| ████████████████ 104500/105600 | Batch Size: 11 | Gen Rate: 9.8kHz | }16000


<class 'numpy.ndarray'>
Duration of audio: 6.8125
Extra time needed: -5.4125
Too long
1
6
Speedup: 4.866071428571429
New Time: 72.40571428571428
Synthesizing new audio...
{| ████████████████ 76000/76800 | Batch Size: 8 | Gen Rate: 7.2kHz | }16000


<class 'numpy.ndarray'>
Duration of audio: 4.9875
Extra time needed: -2.8474999999999997
Too long
2
4
Speedup: 2.330607476635514
New Time: 74.56861678004535
Synthesizing new audio...
{| ████████████████ 38000/38400 | Batch Size: 4 | Gen Rate: 3.3kHz | }16000


<class 'numpy.ndarray'>
Duration of audio: 2.875
Extra time needed: -1.655
Too long
1
2
Speedup: 2.3565573770491803
New Time: 75.81850340136054
Synthesizing new audio...
{| ████████████████ 85500/86400 | Batch Size: 9 | Gen Rate: 8.1kHz | }16000


<class 'numpy.ndarray'>
Duration of audio: 5.65
Extra time needed: -3.1200000000000006
Too long
2
5
Speedup: 2.2332015810276684
New Time: 78.49342403628118
